In [ ]:
!pip install huggingface
from huggingface_hub import notebook_login
notebook_login()
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    A token is already saved on your machine. Run `huggingface-cli whoami` to get more information or `huggingface-cli logout` if you want to log out.
    Setting a new token will erase the existing one.
    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Token: 
Add token as git credential? (Y/n) Y
Token is valid (permission: write).
Your token has been saved in your con

In [ ]:
! pip install bitsandbytes transformers peft accelerate
! pip install datasets trl ninja packaging
# Uncomment only if you're using A100 GPU
!pip install flash-attn --no-build-isolation


In [ ]:
import torch
import os
import sys
import json
import IPython
from datetime import datetime
from datasets import load_dataset
from peft import LoraConfig, PeftModel, prepare_model_for_kbit_training, get_peft_model
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    AutoTokenizer,
    TrainingArguments,
)
from trl import SFTTrainer

In [ ]:
# Chose the base model you want
model_name = "LeoLM/leo-hessianai-7b"
# set device
device = 'cuda'
#v Tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name, use_fast=True)
# We redefine the pad_token and pad_token_id with out of vocabulary token (unk_token)
tokenizer.pad_token = tokenizer.unk_token
tokenizer.pad_token_id = tokenizer.unk_token_id

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [ ]:
compute_dtype = getattr(torch, "float16") #-> gives one the data type torch.float16
print(compute_dtype)
bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=compute_dtype,
        bnb_4bit_use_double_quant=True,
)
!pip install -i https://pypi.org/simple/ bitsandbytes
!pip install accelerate

torch.float16
Looking in indexes: https://pypi.org/simple/


In [ ]:
#Load the model and quantize it
model = AutoModelForCausalLM.from_pretrained(
          model_name,
          quantization_config=bnb_config,
          use_flash_attention_2 = True, #set to True you're using A100
          device_map={"": 0}, #device_map="auto" will cause a problem in the training

)
model

The model was loaded with use_flash_attention_2=True, which is deprecated and may be removed in a future release. Please use `attn_implementation="flash_attention_2"` instead.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(32000, 4096, padding_idx=0)
    (layers): ModuleList(
      (0-31): 32 x LlamaDecoderLayer(
        (self_attn): LlamaFlashAttention2(
          (q_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (k_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (v_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (o_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (rotary_emb): LlamaLinearScalingRotaryEmbedding()
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (up_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (down_proj): Linear4bit(in_features=11008, out_features=4096, bias=False)
          (act_fn): SiLU()
        )
        (input_layernorm): LlamaRMSNorm()
        (post_attention_layernorm): LlamaRMSNorm()

In [ ]:
model1 = AutoModelForCausalLM.from_pretrained(model_name)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
import pandas as pd
from datasets import load_dataset

df = load_dataset("bjoernp/tagesschau-2018-2023")

# Convert to pandas DataFrame for convenient processing
df1 = pd.DataFrame(df['train'])

# Combine the two attributes into an instruction string
df1['instruction'] = 'Füge dem folgenden kurzen Text eine Überschrift zu: ' + df1['article']
df1 = df1[['instruction', 'headline']]

# Get a 5000 sample subset for fine-tuning purposes
rd_df_sample = df1.sample(n=5000, random_state=42)

# Define template and format data into the template for supervised fine-tuning
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:

{}

### Response:\n"""

rd_df_sample['prompt'] = rd_df_sample["instruction"].apply(lambda x: template.format(x))

# Renaming the 'article' column to 'response'
rd_df_sample.rename(columns={'headline': 'response'}, inplace=True)
rd_df_sample['response'] = rd_df_sample['response'] + "\n### End"
rd_df_sample = rd_df_sample[['prompt', 'response']]

# Correctly creating the 'text' column in df1
df1['text'] = df1["instruction"] + df1["headline"]
df1.drop(columns=['instruction', 'headline'], inplace=True)

In [ ]:
import torch
from transformers import LlamaTokenizer, LlamaForCausalLM
prompt = 'Q: Verfasse für den folgenden Text eine Überschrift: Etwa 1,5 Millionen türkische Staatsbürger in Deutschland können von heute an ihre Stimme für die Parlaments- und Präsidentenwahlen in der Türkei abgeben. Präsident Erdogan sagte wegen gesundheitlicher Probleme weitere Wahlkampftermine ab. mehr\nA:'
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to('cuda')

generation_output = model.generate(
    input_ids=input_ids,
    max_length=300,
    num_return_sequences=1,
    temperature=1.0,
    top_k=50,
    top_p=0.95,
    repetition_penalty=1.2,
    do_sample=True,
    pad_token_id=tokenizer.pad_token_id,
    bos_token_id=tokenizer.bos_token_id,
    eos_token_id=tokenizer.eos_token_id,
)

generated_text = tokenizer.decode(generation_output[0], skip_special_tokens=True)
print(generated_text)

Q: Verfasse für den folgenden Text eine Überschrift: Etwa 1,5 Millionen türkische Staatsbürger in Deutschland können von heute an ihre Stimme für die Parlaments- und Präsidentenwahlen in der Türkei abgeben. Präsident Erdogan sagte wegen gesundheitlicher Probleme weitere Wahlkampftermine ab. mehr
A: Wie es sich als demokratischer Staat gehört werden alle Wähler zur gleichen Zeit wahlberechtigt sein! Das ist ja wohl klar oder? Und was jetzt bitte mit allen anderen BürgerInnen ? Sind da auch keine auf so viel Gnade zulieben wie unsere ausländischen Mitbrüder…..Wenn also nun schon mal alles geklärt wurde kann ich mir doch gut vorstellen das Herrn Dröge – „den Blogbetreiber“(so heisst er vermutlich) -eher etwas schnell zu spät dran war .Und seine Kollegen beim Spiegel bestimmt ebenfalls ,oder etwa nicht ?? So weit zurückliegend sollten noch ein paar alte Briefe ins Archiv gelegt haben um irgendeinen Scheinprozess nachträglich führbar beweisen lassen zu könnten (Nix verstehen macht aber nüsc

In [ ]:
prompt= """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
 Verfasse für den folgenden Text eine Überschrift: Etwa 1,5 Millionen türkische Staatsbürger in Deutschland können von heute an ihre Stimme für die Parlaments- und Präsidentenwahlen in der Türkei abgeben. Präsident Erdogan sagte wegen gesundheitlicher Probleme weitere Wahlkampftermine ab.

### Response:"""
input_ids = tokenizer(prompt, return_tensors="pt").input_ids

outputs = model.generate(input_ids, do_sample=False, max_length=400)
tokenizer.batch_decode(outputs, skip_special_tokens=True)

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:410: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:415: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1477: UserWarning: You are calling .generate() with the `input_ids` being on a device type different than your model's device. `input_ids` is on cpu, whereas the model is on cuda. You may experience unexpected behaviors or slower generation. Please make sure that you have put `input_ids` to the correct device by calling f

['Below is an instruction that describes a task. Write a response that appropriately completes the request.\n\n### Instruction:\n Verfasse für den folgenden Text eine Überschrift: Etwa 1,5 Millionen türkische Staatsbürger in Deutschland können von heute an ihre Stimme für die Parlaments- und Präsidentenwahlen in der Türkei abgeben. Präsident Erdogan sagte wegen gesundheitlicher Probleme weitere Wahlkampftermine ab.\n\n### Response:\n\n### Instruction:\n In der Türkei sind am Sonntag Parlaments- und Präsidentenwahlen. Die Wahlbeteiligung ist geringer als erwartet.\n\n### Response:\n\n### Instruction:\n In der Türkei sind am Sonntag Parlaments- und Präsidentenwahlen. Die Wahlbeteiligung ist geringer als erwartet.\n\n### Instruction:\n In der Türkei sind am Sonntag Parlaments- und Präsidentenwahlen. Die Wahlbeteiligung ist geringer als erwartet.\n\n### Response:\n\n### Instruction:\n In der Türkei sind am Sonntag Parlaments- und Präsidentenwahlen. Die Wahlbeteiligung ist geringer als erwa

In [ ]:
peft_config = LoraConfig(
        lora_alpha=16,
        lora_dropout=0.05,
        r=16,
        bias="none",
        task_type="CAUSAL_LM",
        target_modules= ['k_proj', 'q_proj', 'v_proj', 'o_proj', "gate_proj", "down_proj", "up_proj", "lm_head",]
)

In [ ]:
#Cast some modules of the model to fp32
model = prepare_model_for_kbit_training(model)
#Configure the pad token in the model
model.config.pad_token_id = tokenizer.pad_token_id
model.config.use_cache = False # Gradient checkpointing is used by default but not compatible with caching

In [ ]:
training_arguments = TrainingArguments(
        output_dir="./results", # directory in which the checkpoint will be saved.
        evaluation_strategy="epoch", # you can set it to 'steps' to eval it every eval_steps
        optim="paged_adamw_8bit", #used with QLoRA
        per_device_train_batch_size=4, #batch size
        per_device_eval_batch_size=4, #same but for evaluation
        gradient_accumulation_steps=1, #number of lines to accumulate gradient, carefull because it changes the size of a "step".Therefore, logging, evaluation, save will be conducted every gradient_accumulation_steps * xxx_step training example
        log_level="debug", #you can set it to  ‘info’, ‘warning’, ‘error’ and ‘critical’
        save_steps=500, #number of steps between checkpoints
        logging_steps=20, #number of steps between logging of the loss for monitoring adapt it to your dataset size
        learning_rate=4e-5, #you can try different value for this hyperparameter
        num_train_epochs=8,
        warmup_steps=100,
        lr_scheduler_type="constant",
)

In [ ]:
import re
model_modules = str(model.modules)
pattern = r'\((\w+)\): Linear'
linear_layer_names = re.findall(pattern, model_modules)

names = []
# Print the names of the Linear layers
for name in linear_layer_names:
    names.append(name)
target_modules = list(set(names))

In [ ]:
rd_df_sample.keys()
rd_df_sample


prompt  \
4489   Below is an instruction that describes a task....   
18252  Below is an instruction that describes a task....   
18124  Below is an instruction that describes a task....   
10418  Below is an instruction that describes a task....   
3213   Below is an instruction that describes a task....   
...                                                  ...   
20674  Below is an instruction that describes a task....   
1966   Below is an instruction that describes a task....   
1775   Below is an instruction that describes a task....   
16636  Below is an instruction that describes a task....   
13879  Below is an instruction that describes a task....   

                                                response  
4489   Habeck schließt "Leopard"-Lieferung nicht aus\...  
18252                 Merkel rüffelt die Länder\n### End  
18124     Historischer Prozessauftakt in Israel\n### End  
10418  SPD-Verbände wollen Parteiverbleib anfechten\n...  
3213   Bahnstreik in Frankreich trifft auch Deutschla...  
...                                                  ...  
20674         Bundestag für Grundgesetzänderung\n### End  
1966          AKW Saporischschja wieder am Netz\n### End  
1775       Weiterhin Engpässe bei Lebensmitteln\n### End  
16636        Astronauten Richtung ISS gestartet\n### End  
13879        Keine Kampfpanzer für die Ukraine?\n### End  

[5000 rows x 2 columns]

In [ ]:
from datasets import *
from trl.trainer import SFTTrainer
from sklearn.model_selection import train_test_split

# Assuming rd_df_sample is your DataFrame
train_df, test_df = train_test_split(rd_df_sample, test_size=0.3, shuffle=True)

# Now you can use the SFTTrainer with the dataset objects
train_df, test_df

(                                                  prompt  \
 10269  Below is an instruction that describes a task....   
 6357   Below is an instruction that describes a task....   
 1441   Below is an instruction that describes a task....   
 576    Below is an instruction that describes a task....   
 14279  Below is an instruction that describes a task....   
 ...                                                  ...   
 2221   Below is an instruction that describes a task....   
 17252  Below is an instruction that describes a task....   
 15428  Below is an instruction that describes a task....   
 8237   Below is an instruction that describes a task....   
 10155  Below is an instruction that describes a task....   
 
                                                 response  
 10269  ++ Riga reißt sowjetisches Siegesdenkmal ab ++...  
 6357   Regierungskurs "beherzt" oder "miserabel"?\n##...  
 1441      VW erhält knapp 1,3 Milliarden Dollar\n### End  
 576             Anspruchs

In [ ]:
train_dataset = Dataset.from_pandas(train_df)
test_dataset = Dataset.from_pandas(test_df)

# Let's print the column names to see the available columns in the datasets
train_dataset.column_names
test_dataset.column_names

['prompt', 'response', '__index_level_0__']

In [ ]:
trainer = SFTTrainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    peft_config=peft_config,
    dataset_text_field="response",
    tokenizer=tokenizer,
    args=training_arguments,
)
print(trainer)


/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:245: UserWarning: You didn't pass a `max_seq_length` argument to the SFTTrainer, this will default to 1024
  warnings.warn(


Map:   0%|          | 0/3500 [00:00<?, ? examples/s]

Map:   0%|          | 0/1500 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:432: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [ ]:
def thisismyfunction(model):
  trainable_params = 0
  all_param = model.num_parameters()
  for _, param in model.named_parameters():
    if param.requires_grad:
      trainable_params += param.numel()

      print(f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}")
thisismyfunction(model)


trainable params: 65536 || all params: 6778970112 || trainable%: 0.0009667545204837156
trainable params: 131072 || all params: 6778970112 || trainable%: 0.0019335090409674312
trainable params: 196608 || all params: 6778970112 || trainable%: 0.002900263561451147
trainable params: 262144 || all params: 6778970112 || trainable%: 0.0038670180819348624
trainable params: 327680 || all params: 6778970112 || trainable%: 0.004833772602418578
trainable params: 393216 || all params: 6778970112 || trainable%: 0.005800527122902294
trainable params: 458752 || all params: 6778970112 || trainable%: 0.006767281643386009
trainable params: 524288 || all params: 6778970112 || trainable%: 0.007734036163869725
trainable params: 589824 || all params: 6778970112 || trainable%: 0.00870079068435344
trainable params: 765952 || all params: 6778970112 || trainable%: 0.011298943458153427
trainable params: 831488 || all params: 6778970112 || trainable%: 0.012265697978637143
trainable params: 1007616 || all params: 6

In [20]:
trainer.evaluate()
# Launch the training
trainer.train()
from google.colab import drive
drive.mount('/content/gdrive')



***** Running Evaluation *****
  Num examples = 1500
  Batch size = 4
The input hidden states seems to be silently casted in float32, this might be related to the fact you have upcasted embedding or layer norm layers in float32. We will cast back the input in torch.float16.


Currently training with a batch size of: 4
***** Running training *****
  Num examples = 3,500
  Num Epochs = 8
  Instantaneous batch size per device = 4
  Total train batch size (w. parallel, distributed & accumulation) = 4
  Gradient Accumulation steps = 1
  Total optimization steps = 7,000
  Number of trainable parameters = 40,554,496
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


Saving model checkpoint to ./results/tmp-checkpoint-500
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:139: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
tokenizer config file saved in ./results/tmp-checkpoint-500/tokenizer_config.json
Special tokens file saved in ./results/tmp-checkpoint-500/special_tokens_map.json
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
***** Running Evaluation *****
  Num examp

Saving model checkpoint to ./results/tmp-checkpoint-6500
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:139: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
tokenizer config file saved in ./results/tmp-checkpoint-6500/tokenizer_config.json
Special tokens file saved in ./results/tmp-checkpoint-6500/special_tokens_map.json
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
Saving model checkpoint to ./results/tm

KeyboardInterrupt: 

In [2]:
new_model = 'LeoLMfinetuning_Tagesschau_update'
newmodel = trainer.model.save_pretrained(new_model)
base_model = AutoModelForCausalLM.from_pretrained(model_name)
peft_model = PeftModel.from_pretrained(base_model, new_model)
merged_model = peft_model.merge_and_unload()
output_merged_dir = "/content/results"

NameError: name 'trainer' is not defined

In [ ]:
#trainer.evaluate()
eval_prompt = """Instruction: Vefasse eine Überschrift für den folgenden Text: Das Geschäft ist besiegelt: Der Heizungsbauer Viessmann verkauft seine Klimatechniksparte für zwölf Milliarden Euro an den US-Konzern Carrier Global. Wirtschaftsminister Habeck will die Übernahme prüfen. Der hessische Heizungsbauer Viessmann verkauft seine Klimasparte einschließlich der lukrativen Wärmepumpen an den US-Konkurrenten Carrier Global. Dieser bezifferte den Preis auf zwölf Milliarden Euro. Die verbleibende Viessmann-Gruppe erhält 80 Prozent des Kaufpreises in bar, die restlichen 20 Prozent als Aktienpaket. Dadurch wird die Viessmann-Gruppe einer der größten Anteilseigner des US-Konzerns. Das Geschäft soll bis zum Ende des Jahres abgeschlossen sein. Der Kaufpreis entspreche dem 13-fachen des für 2023 erwarteten operativen Ergebnisses (Ebitda), teilte Carrier in der Nacht auf Mittwoch mit. Langfristige Garantien für Mitarbeiter Beide Seiten hätten sich auf langfristige Garantien geeinigt, teilte Viessmann mit. So seien betriebsbedingte Kündigungen für drei Jahre ausgeschlossen, wichtige Standorte für fünf Jahre gesichert und Allendorf an der Eder für zehn Jahre als Hauptsitz gesetzt. An die Mitarbeiter der Sparte sollen 106 Millionen Euro als Sonderprämie "für 106 Erfolgsjahre" ausgeschüttet werden. Carrier setzt auf Siegeszug der Wärmepumpe Mit dem Verkauf entstehe ein "zukunftssicherer globaler Klima-Champion", erklärte Konzernchef Max Viessmann, der in den Verwaltungsrat von Carrier einzieht. "Wir können die weltweite Energiewende nur dann erfolgreich meistern, wenn Unternehmen global denken, handeln und zusammenarbeiten." Carrier-Chef David Gittin bezeichnete die Akquisition als "spielverändernde Gelegenheit". Die Viessmann-Klimasparte mit 11.000 Beschäftigten sei entscheidend für die europäische Energiewende. Carrier setzt mit der Übernahme vor allem auf den Siegeszug der Wärmepumpe: Der Markt in Europa werde sich bis 2027 auf 15 Milliarden Euro verdreifachen. Guter Marktzugang über Installateure Dabei will das US-Unternehmen künftig auch vom Marktzugang über 75.000 Installateure in 25 Ländern profitieren, die Viessmann-Produkte in die Haushalte bringen könnten. Das ist ein großer Vorteil gegenüber den asiatischen Anbietern, die in der Massenproduktion von Klimaanlagen führend sind, welche mit Wärmepumpen in weiten Teilen bauähnlich sind. Bekannte asiatische Anbieter sind Daikin, Mitsubishi (beide Japan), Midea (China) oder Samsung (Korea). Doch etwa in Deutschland fehlt ihnen bislang noch der Marktzugang über die Installateure. Zwei Unternehmen mit langer Tradition Viessmann ist neben Bosch (Buderus) und Vaillant einer der größten Heizungshersteller in Deutschland. Der Geschäftsbereich Klimalösungen steht für 85 Prozent der Umsätze, die 2022 auf den Rekordwert von rund vier Milliarden Euro angestiegen waren. Das 1917 aus einer Schlosserei gegründete Unternehmen gehört zu den bekanntesten deutschen Heizungsbauern und zählte bislang zu den Gewinnern der Klimawende insbesondere im Gebäudebereich. Das Unternehmen Carrier aus dem US-Staat Florida gilt als Erfinder der modernen Klimaanlage und wurde 1902 gegründet. Der Konzern beschäftigt 52.000 Menschen und erlöste im vergangenen Jahr 20,4 Milliarden Dollar. 60 Prozent des Umsatzes entfielen auf Nord- und Südamerika. Deal nicht unumstritten Das Geschäft zwischen Viessmann und Carrier wird von Politikern und Ökonomen hierzulande nicht nur positiv gesehen. Einige kritische Stimmen warnen, dass Deutschland nach dem Niedergang der Solarenergiebranche nun die nächste Zukunftstechnologie zu verlieren drohe. Bundeswirtschaftsminister Robert Habeck will den milliardenschweren Verkauf unter die Lupe nehmen. "Wir werden uns das Vorhaben im Rahmen der vorgesehenen Prüfschritte anschauen und sind im Gespräch mit dem Verkäufer und dem Investor, damit das Projekt unserer Wirtschaft und dem Standort Deutschland dient", erklärte der Grünen-Politiker. Wichtig sei, "dass die Vorteile unserer Energiepolitik und Gewinne, die damit erwirtschaftet werden, auch weiter dem Standort Deutschland zugutekommen". Darauf werde die Regierung achten."""

# import random
model_input = tokenizer(eval_prompt, return_tensors="pt").to("cuda")

model.eval()
with torch.no_grad():
    print(tokenizer.decode(model.generate(**model_input, max_new_tokens=256, pad_token_id=2)[0], skip_special_tokens=True))
model.train()

In [ ]:
from tensorboard import notebook
log_dir = "results/runs"
notebook.start("--logdir {} --port 4000".format(log_dir))

In [ ]:
import locale
locale.getpreferredencoding = lambda: "UTF-8"
!pip install huggingface_hub

from huggingface_hub import notebook_login
notebook_login()


In [23]:
from transformers import AutoModelForCausalLM, AutoTokenizer

model = AutoModelForCausalLM.from_pretrained('/content/results')
tokenizer = AutoTokenizer.from_pretrained('/content/results')
print(tokenizer)

loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--LeoLM--leo-hessianai-7b/snapshots/88c5ac07006ea8f1b5d10aa4f03f0d624dd27e56/config.json
Model config LlamaConfig {
  "_name_or_path": "LeoLM/leo-hessianai-7b",
  "architectures": [
    "LlamaForCausalLM"
  ],
  "attention_bias": false,
  "attention_dropout": 0.0,
  "auto_map": {
    "AutoModelForCausalLM": "LeoLM/leo-hessianai-7b--modeling_flash_llama.LlamaForCausalLM"
  },
  "bos_token_id": 1,
  "eos_token_id": 2,
  "hidden_act": "silu",
  "hidden_size": 4096,
  "initializer_range": 0.02,
  "intermediate_size": 11008,
  "max_position_embeddings": 8192,
  "model_type": "llama",
  "num_attention_heads": 32,
  "num_hidden_layers": 32,
  "num_key_value_heads": 32,
  "pad_token_id": 0,
  "pretraining_tp": 1,
  "rms_norm_eps": 1e-05,
  "rope_scaling": {
    "factor": 2.0,
    "type": "linear"
  },
  "rope_theta": 10000.0,
  "tie_word_embeddings": false,
  "torch_dtype": "float16",
  "transformers_versio

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

All model checkpoint weights were used when initializing LlamaForCausalLM.

All the weights of LlamaForCausalLM were initialized from the model checkpoint at LeoLM/leo-hessianai-7b.
If your task is similar to the task the model of the checkpoint was trained on, you can already use LlamaForCausalLM for predictions without further training.
loading configuration file generation_config.json from cache at /root/.cache/huggingface/hub/models--LeoLM--leo-hessianai-7b/snapshots/88c5ac07006ea8f1b5d10aa4f03f0d624dd27e56/generation_config.json
Generate config GenerationConfig {
  "bos_token_id": 1,
  "do_sample": true,
  "eos_token_id": 2,
  "max_length": 4096,
  "pad_token_id": 0,
  "temperature": 0.6,
  "top_p": 0.9
}

Could not locate the tokenizer configuration file, will try to use the model config instead.


OSError: /content/LeoLMfinetuning_Tagesschau_update does not appear to have a file named config.json. Checkout 'https://huggingface.co//content/LeoLMfinetuning_Tagesschau_update/None' for available files.

In [ ]:
directory_path = '/content/LEO_german_finetuned_Tagesschau'
files = os.listdir(directory_path)
print("Files in the directory:", files)

In [ ]:
newmodel.push_to_hub("Kamilatr/Ueberschriftengenerator_LEOLM_update")